<a href="https://www.kaggle.com/code/thakshayan/amex-lightgbm-code?scriptVersionId=116583882" target="_blank"><img align="left" alt="Kaggle" title="Open in Kaggle" src="https://kaggle.com/static/images/open-in-kaggle.svg"></a>

In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-`1qonly "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/amex-data-integer-dtypes-parquet-format/train.parquet
/kaggle/input/amex-data-integer-dtypes-parquet-format/test.parquet
/kaggle/input/amex-default-prediction/sample_submission.csv
/kaggle/input/amex-default-prediction/train_data.csv
/kaggle/input/amex-default-prediction/test_data.csv
/kaggle/input/amex-default-prediction/train_labels.csv


In [2]:
import os
os.environ['TF_CPP_MIN_LOG_LEVEL'] = '3'
import os


import lightgbm
from xgboost import XGBClassifier

import matplotlib.pyplot as plt
import seaborn as sbn
import numpy as np
import pandas as pd
import warnings

from sklearn.preprocessing import LabelEncoder
from sklearn.impute import SimpleImputer
from sklearn.model_selection import cross_val_score
from sklearn.metrics import confusion_matrix, classification_report, roc_curve, auc, RocCurveDisplay, accuracy_score

import shap
import itertools

In [3]:
train = pd.read_parquet("/kaggle/input/amex-data-integer-dtypes-parquet-format/train.parquet")
test = pd.read_parquet("/kaggle/input/amex-data-integer-dtypes-parquet-format/test.parquet")
train_labels = pd.read_csv("../input/amex-default-prediction/train_labels.csv")
#submission = pd.read_csv("/kaggle/input/amex-default-prediction/sample_submission.csv")


# Describe

In [4]:
train.shape, test.shape, train_labels.shape

((5531451, 190), (11363762, 190), (458913, 2))

In [5]:
train.duplicated().sum()

0

In [6]:
for col in train.columns.values:
  print(col,'-',train[col].isna().sum()/len(train[col]))

customer_ID - 0.0
S_2 - 0.0
P_2 - 0.008313370216964771
D_39 - 0.0
B_1 - 0.0
B_2 - 0.00036446133211701597
R_1 - 0.0
S_3 - 0.1844984254583472
D_41 - 0.00036446133211701597
B_3 - 0.00036446133211701597
D_42 - 0.8569427804747796
D_43 - 0.29981211078250536
D_44 - 0.0
B_4 - 0.0
D_45 - 0.000364642116507947
B_5 - 0.0
R_2 - 0.0
D_46 - 0.21905626570677386
D_47 - 0.0
D_48 - 0.12993426137192574
D_49 - 0.0
B_6 - 4.212276308693686e-05
B_7 - 0.0
B_8 - 0.004025706817252833
D_50 - 0.5680972316305433
D_51 - 0.0
B_9 - 0.0
R_3 - 0.0
D_52 - 0.005344528949094912
P_3 - 0.05450504759058699
B_10 - 0.0
D_53 - 0.7384292114311417
S_5 - 0.0
B_11 - 0.0
S_6 - 0.0
D_54 - 0.00036446133211701597
R_4 - 0.0
S_7 - 0.1844984254583472
B_12 - 0.0
S_8 - 0.0
D_55 - 0.03340949779723259
D_56 - 0.5407158085645158
B_13 - 0.008952262254515135
R_5 - 0.0
D_58 - 0.0
S_9 - 0.5303568629641662
B_14 - 0.0
D_59 - 0.0
D_60 - 0.0
D_61 - 0.10811846656510199
B_15 - 0.001251570338415725
S_11 - 0.0
D_62 - 0.137063674612683
D_63 - 0.0
D_64 - 0.0


In [7]:
non_numeric_cols = train.columns[train.dtypes == 'object'].values
non_numeric_cols

array(['customer_ID', 'S_2'], dtype=object)

In [8]:
numeric_cols = train.columns[train.dtypes != 'object'].values
numeric_cols

array(['P_2', 'D_39', 'B_1', 'B_2', 'R_1', 'S_3', 'D_41', 'B_3', 'D_42',
       'D_43', 'D_44', 'B_4', 'D_45', 'B_5', 'R_2', 'D_46', 'D_47',
       'D_48', 'D_49', 'B_6', 'B_7', 'B_8', 'D_50', 'D_51', 'B_9', 'R_3',
       'D_52', 'P_3', 'B_10', 'D_53', 'S_5', 'B_11', 'S_6', 'D_54', 'R_4',
       'S_7', 'B_12', 'S_8', 'D_55', 'D_56', 'B_13', 'R_5', 'D_58', 'S_9',
       'B_14', 'D_59', 'D_60', 'D_61', 'B_15', 'S_11', 'D_62', 'D_63',
       'D_64', 'D_65', 'B_16', 'B_17', 'B_18', 'B_19', 'D_66', 'B_20',
       'D_68', 'S_12', 'R_6', 'S_13', 'B_21', 'D_69', 'B_22', 'D_70',
       'D_71', 'D_72', 'S_15', 'B_23', 'D_73', 'P_4', 'D_74', 'D_75',
       'D_76', 'B_24', 'R_7', 'D_77', 'B_25', 'B_26', 'D_78', 'D_79',
       'R_8', 'R_9', 'S_16', 'D_80', 'R_10', 'R_11', 'B_27', 'D_81',
       'D_82', 'S_17', 'R_12', 'B_28', 'R_13', 'D_83', 'R_14', 'R_15',
       'D_84', 'R_16', 'B_29', 'B_30', 'S_18', 'D_86', 'D_87', 'R_17',
       'R_18', 'D_88', 'B_31', 'S_19', 'R_19', 'B_32', 'S_20', 'R_20',
 

In [9]:
# import seaborn as sns
# for i in numeric_cols:
#     X = train[i].round(decimals = 3)
#     plt.figure(i)
#     ax = sns.countplot(X)
#     ax.set_xticklabels(ax.get_xticklabels(), rotation=40, fontsize=5)
#     plt.tight_layout()
#     plt.show()        

# Preprocessing

In [10]:
import matplotlib.style as style
import seaborn as sns
style.use('seaborn-poster')
sns.set_style('ticks')
plt.subplots(figsize = (270,200))
## Plotting heatmap. 

# Generate a mask for the upper triangle (taken from seaborn example gallery)
mask = np.zeros_like(train.corr(), dtype=np.bool)
mask[np.triu_indices_from(mask)] = True


sns.heatmap(train.corr(), cmap=plt.get_cmap('Blues'), annot=True, mask=mask, center = 0, square=True, 
             );
## Give title. 
plt.title("Heatmap of all the Features", fontsize = 25);

`np.bool` is a deprecated alias for the builtin `bool`. To silence this warning, use `bool` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.bool_` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations


# Preprocessing Train

In [11]:
train['Date'] =  pd.to_datetime(train['S_2'], format="%Y/%m/%d")
train['weekday'] = train['Date'].dt.weekday
train['day'] = train['Date'].dt.day
train['month'] = train['Date'].dt.month
train['year'] = train['Date'].dt.year

In [12]:
train['S_2'] = pd.to_numeric(train['S_2'].str.replace('-',''))
train['S_2']

0          20170309
1          20170407
2          20170528
3          20170613
4          20170716
             ...   
5531446    20171105
5531447    20171223
5531448    20180106
5531449    20180206
5531450    20180314
Name: S_2, Length: 5531451, dtype: int64

In [13]:
train.drop(['Date'], axis=1, inplace=True)
train.shape

(5531451, 194)

In [14]:
cat_features = ["B_30","B_38","D_114","D_116","D_117","D_120","D_126","D_63","D_64","D_66","D_68",'customer_ID']

In [15]:
features = [col for col in train.columns.values if col not in cat_features]
features.append('customer_ID')

In [16]:
for i in cat_features:
    if train[i].dtype == 'int64':
        train.astype('int16')

In [17]:
train_cat = train[cat_features].groupby('customer_ID',as_index=False).agg(['last', 'nunique'])
train_cat.shape

(458913, 22)

In [18]:
for i in train.columns:
    if train[i].dtype == 'float64':
        train.astype('float16')

In [19]:
drop_features = ["B_30","B_38","D_114","D_116","D_117","D_120","D_126","D_63","D_64","D_66","D_68"]

In [20]:
train.drop(drop_features, axis=1, inplace=True)

In [21]:
train = train.groupby('customer_ID',as_index=False).agg(['mean', 'std', 'sum','last'])

train.shape

(458913, 728)

In [22]:
import gc
gc.collect()

1087438

In [23]:
train = train.merge(train_cat, how='inner', on="customer_ID")
train.shape

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`


(458913, 750)

In [24]:
del train_cat

In [25]:
join_col = []
for i in train.columns.values:
    if type(i) is tuple:
        col = '_'.join(i)
        join_col.append(col)
train.columns = join_col
train.reset_index()

customer_ID      S_2_mean  \
0       0000099d6bd597052cdcda90ffabf56573fe9d7c79be5f...  2.017294e+07   
1       00000fd6641609c6ece5454664794f0340ad84dddce9a2...  2.017295e+07   
2       00001b22f846c82c51f6e3958ccd81970162bae8b007e8...  2.017294e+07   
3       000041bdba6ecadd89a52d11886e8eaaec9325906c9723...  2.017295e+07   
4       00007889e4fcd2614b6cbe7f8f3d2e5c728eca32d9eb8a...  2.017296e+07   
...                                                   ...           ...   
458908  ffff41c8a52833b56430603969b9ca48d208e7c192c6a4...  2.017295e+07   
458909  ffff518bb2075e4816ee3fe9f3b152c57fc0e6f01bf7fd...  2.017295e+07   
458910  ffff9984b999fccb2b6127635ed0736dda94e544e67e02...  2.017294e+07   
458911  ffffa5c46bc8de74f5a4554e74e239c8dee6b9baf38814...  2.017295e+07   
458912  fffff1d38b785cef84adeace64f8f83db3a0c31e8d92ea...  2.017295e+07   

            S_2_std    S_2_sum  S_2_last  P_2_mean   P_2_std    P_2_sum  \
0       4153.551914  262248272  20180313  0.933824  0.024194  12.139710   
1       4153.102929  262248343  20180325  0.899820  0.022119  11.697656   
2       4152.423559  262248247  20180312  0.878454  0.028911  11.419907   
3       4150.147254  262248372  20180329  0.598969  0.020107   7.786597   
4       4154.677120  262248430  20180330  0.891679  0.042325  11.591827   
...             ...        ...       ...       ...       ...        ...   
458908  4157.364072  262248288  20180331  0.848750  0.041969  11.033751   
458909  4153.126694  262248363  20180322  0.859327  0.012425  11.171254   
458910  4150.841853  262248238  20180307  0.786838  0.014312  10.228889   
458911  4153.138683  262248355  20180323  0.804454  0.037442  10.457907   
458912  4149.196218  262248290  20180314  0.983617  0.012879  12.787016   

        P_2_last  D_39_mean  ...  D_126_last  D_126_nunique  D_63_last  \
0       0.934745   0.230769  ...           2              1          0   
1       0.880519   7.153846  ...           2              1          3   
2       0.880875   0.000000  ...           2              1          3   
3       0.621776   1.538462  ...           2              1          3   
4       0.871900   0.000000  ...           2              1          3   
...          ...        ...  ...         ...            ...        ...   
458908  0.844229   3.846154  ...           2              1          3   
458909  0.831279   2.076923  ...           2              1          3   
458910  0.800522   7.384615  ...           2              1          3   
458911  0.754129   0.923077  ...           2              1          3   
458912  0.982175   9.769231  ...           2              1          4   

        D_63_nunique  D_64_last  D_64_nunique  D_66_last  D_66_nunique  \
0                  1          0             1         -1             1   
1                  1          0             1         -1             1   
2                  1          2             1         -1             1   
3                  1          0             1         -1             1   
4                  1          0             1          1             1   
...              ...        ...           ...        ...           ...   
458908             1          3             1          1             1   
458909             1          2             1         -1             1   
458910             1          3             1         -1             1   
458911             1          3             2         -1             1   
458912             1          0             2         -1             1   

        D_68_last  D_68_nunique  
0               6             1  
1               6             1  
2               6             1  
3               3             3  
4               6             1  
...           ...           ...  
458908          6             1  
458909          6             1  
458910          5             1  
458911          3             2  
458912          5             2  

[458913 rows x 751 columns]

In [26]:
train = train.merge(train_labels, how='inner', on="customer_ID")
train.shape

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`


(458913, 752)

In [27]:
corr_matrix = train.corr().abs()

# Select upper triangle of correlation matrix
upper = corr_matrix.where(np.triu(np.ones(corr_matrix.shape), k=1).astype(np.bool))

# Find features with correlation greater than 0.95
to_drop = [column for column in upper.columns if any(upper[column] >= 0.99)]

# Drop features 

to_drop

`np.bool` is a deprecated alias for the builtin `bool`. To silence this warning, use `bool` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.bool_` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations


['D_45_sum',
 'B_5_sum',
 'S_5_sum',
 'B_11_mean',
 'B_11_std',
 'B_11_sum',
 'B_11_last',
 'B_12_sum',
 'B_12_last',
 'B_13_sum',
 'B_14_sum',
 'B_15_sum',
 'B_20_sum',
 'D_71_sum',
 'B_23_mean',
 'B_23_std',
 'B_23_sum',
 'B_23_last',
 'D_75_mean',
 'D_75_sum',
 'D_77_sum',
 'S_18_sum',
 'D_86_sum',
 'B_31_sum',
 'B_32_sum',
 'R_23_sum',
 'D_92_sum',
 'D_94_sum',
 'S_26_sum',
 'D_104_sum',
 'D_104_last',
 'B_36_sum',
 'B_37_mean',
 'B_37_std',
 'B_37_sum',
 'B_37_last',
 'R_26_last',
 'R_27_last',
 'B_40_sum',
 'D_119_mean',
 'D_119_sum',
 'D_119_last',
 'D_121_last',
 'D_137_mean',
 'D_137_sum',
 'D_141_last',
 'D_143_mean',
 'D_143_std',
 'D_143_sum',
 'D_143_last',
 'day_last',
 'month_sum',
 'year_mean',
 'year_std',
 'year_sum']

In [28]:
len(to_drop)

55

In [29]:
train.drop(to_drop, axis=1, inplace=True)
train.shape

(458913, 697)

# Preprocessing Test

In [30]:
test = pd.read_parquet("/kaggle/input/amex-data-integer-dtypes-parquet-format/test.parquet")

In [31]:
test['Date'] =  pd.to_datetime(test['S_2'], format="%Y/%m/%d")
test['weekday'] = test['Date'].dt.weekday
test['day'] = test['Date'].dt.day
test['month'] = test['Date'].dt.month
test['year'] = test['Date'].dt.year

In [32]:
test['S_2'] = pd.to_numeric(test['S_2'].str.replace('-',''))
test['S_2']

0           20190219
1           20190325
2           20190425
3           20190520
4           20190615
              ...   
11363757    20181219
11363758    20190119
11363759    20190217
11363760    20190319
11363761    20190418
Name: S_2, Length: 11363762, dtype: int64

In [33]:
test.drop(['Date'], axis=1, inplace=True)
test.shape

(11363762, 194)

In [34]:
cat_features = ["B_30","B_38","D_114","D_116","D_117","D_120","D_126","D_63","D_64","D_66","D_68",'customer_ID']

In [35]:
for i in test.columns.values:
    if test[i].dtype == 'int64' and i == 'customer_ID':
        test.astype('int16')

In [36]:
test.shape

(11363762, 194)

In [37]:
test_copy = test[cat_features].groupby('customer_ID',as_index=False).agg([ 'last', 'nunique'])

In [38]:
for i in test.columns.values:
    if test[i].dtype == 'float64':
        test.astype('float16')

In [39]:
drp_col = ['B_30', 'B_38', 'D_114', 'D_116', 'D_117', 'D_120', 'D_126', 'D_63', 'D_64', 'D_66', 'D_68']

In [40]:
test.drop(drp_col, axis=1, inplace=True)

In [41]:
import gc
gc.collect()

84

In [42]:
test = test.groupby('customer_ID',as_index=False).agg(['mean', 'std', 'sum','last'])
test.shape

(924621, 728)

In [43]:
test.shape

(924621, 728)

In [44]:
test = test.merge(test_copy, how='inner', on="customer_ID")


In [45]:
join_col = []
for i in test.columns.values:
    if type(i) is tuple:
        col = '_'.join(i)
        join_col.append(col)
        
test.columns = join_col
test.reset_index()

customer_ID      S_2_mean  \
0       00000469ba478561f23a92a868bd366de6f6527a684c9a...  2.019062e+07   
1       00001bf2e77ff879fab36aa4fac689b9ba411dae63ae39...  2.018373e+07   
2       0000210045da4f81e5f122c6bde5c2a617d03eef67f82c...  2.018838e+07   
3       00003b41e58ede33b8daf61ab56d9952f17c9ad1c3976c...  2.018373e+07   
4       00004b22eaeeeb0ec976890c1d9bfc14fd9427e98c4ee9...  2.018839e+07   
...                                                   ...           ...   
924616  ffff952c631f2c911b8a2a8ca56ea6e656309a83d2f64c...  2.018372e+07   
924617  ffffcf5df59e5e0bba2a5ac4578a34e2b5aa64a1546cd3...  2.018839e+07   
924618  ffffd61f098cc056dbd7d2a21380c4804bbfe60856f475...  2.018372e+07   
924619  ffffddef1fc3643ea179c93245b68dca0f36941cd83977...  2.018372e+07   
924620  fffffa7cf7e453e1acc6a1426475d5cb9400859f82ff61...  2.018567e+07   

            S_2_std    S_2_sum  S_2_last  P_2_mean   P_2_std    P_2_sum  \
0        272.048249  181715574  20191012  0.601387  0.020190   5.412481   
1       4543.779982  262388428  20190415  0.862166  0.031436  11.208157   
2       4154.898704  262448967  20191016  0.748955  0.061456   9.736409   
3       4548.392383  262388444  20190422  0.474728  0.028856   6.171459   
4       4148.441635  262449018  20191022  0.324100  0.049865   4.213296   
...             ...        ...       ...       ...       ...        ...   
924616  4545.595219  262388382  20190414  0.631613  0.015759   8.210974   
924617  4151.105418  262449041  20191019  0.547049  0.053224   7.111636   
924618  4543.301527  262388406  20190406  0.239070  0.048398   3.107911   
924619  4543.890199  262388336  20190408  0.559902  0.017193   7.278728   
924620  4919.059223  161485346  20190418  0.444808  0.014086   3.558466   

        P_2_last  D_39_mean  ...  D_126_last  D_126_nunique  D_63_last  \
0       0.568930   2.222222  ...           1              1          0   
1       0.841177   5.076923  ...           2              1          3   
2       0.697522   6.000000  ...           1              2          0   
3       0.513186  15.846154  ...           2              1          4   
4       0.254478  11.846154  ...           1              1          3   
...          ...        ...  ...         ...            ...        ...   
924616  0.646915   0.000000  ...           2              1          3   
924617  0.471303   1.769231  ...           2              1          3   
924618  0.206425   7.769231  ...           2              1          0   
924619  0.570670   3.615385  ...           2              1          3   
924620  0.454546   0.000000  ...           2              1          3   

        D_63_nunique  D_64_last  D_64_nunique  D_66_last  D_66_nunique  \
0                  1          3             2         -1             1   
1                  1          0             1         -1             1   
2                  1          3             2          1             1   
3                  1          2             1         -1             1   
4                  1          2             2         -1             1   
...              ...        ...           ...        ...           ...   
924616             1          0             1         -1             1   
924617             1          0             1         -1             1   
924618             1          0             1         -1             1   
924619             1          3             2         -1             1   
924620             1          2             1         -1             1   

        D_68_last  D_68_nunique  
0               6             2  
1               6             1  
2               4             2  
3               5             1  
4               5             2  
...           ...           ...  
924616          6             1  
924617          6             2  
924618          6             1  
924619          5             2  
924620          6             1  

[924621 rows x 751 columns]

In [46]:
test.drop(to_drop, axis=1, inplace=True)
test.shape

(924621, 695)

In [47]:
del test_copy


In [48]:
import gc
gc.collect()

42

# Training

In [49]:
target = train['target']
Features = train.drop('target', axis=1, inplace=False)
train.shape, Features.shape

((458913, 697), (458913, 696))

In [50]:
numeric_cols = Features.columns[Features.dtypes != "object"].values
non_numeric_cols = Features.columns[Features.dtypes == 'object'].values

In [51]:
#test_1 = test.loc[:, Features.columns]
test.shape

(924621, 695)

In [52]:
Features.shape, test.shape

((458913, 696), (924621, 695))

In [53]:
from sklearn.preprocessing import StandardScaler
from sklearn.impute import SimpleImputer
from sklearn.compose import ColumnTransformer

from sklearn.pipeline import Pipeline

from sklearn.preprocessing import OneHotEncoder, LabelEncoder, OrdinalEncoder

In [54]:

numeric_preprocessing_steps = Pipeline(steps=[
    ('standard_scaler', StandardScaler()),
    ('imputer', SimpleImputer(strategy='mean')),
    ])

non_numeric_preprocessing_steps = Pipeline(steps=[
    ('imputer', SimpleImputer(strategy='constant', fill_value='missing')),
    #('onehot', OrdinalEncoder())
    ('onehot', OneHotEncoder(handle_unknown='ignore'))
    ])


preprocessor = ColumnTransformer(
    transformers = [
        ("numeric", numeric_preprocessing_steps, numeric_cols),
        #("non_numeric",non_numeric_preprocessing_steps,non_numeric_cols)
    ],
    remainder='drop'
)

# Testing score

In [55]:
from sklearn.model_selection import train_test_split

X_train, X_eval, y_train, y_eval = train_test_split(  
    Features,
    train['target'],
    test_size=0.3,
    shuffle=True,
    random_state=8
)

In [56]:
def amex_metric(y_true: pd.DataFrame, y_pred: pd.DataFrame) -> float:

    def top_four_percent_captured(y_true: pd.DataFrame, y_pred: pd.DataFrame) -> float:
        df = (pd.concat([y_true, y_pred], axis='columns')
              .sort_values('prediction', ascending=False))
        df['weight'] = df['target'].apply(lambda x: 20 if x==0 else 1)
        four_pct_cutoff = int(0.04 * df['weight'].sum())
        df['weight_cumsum'] = df['weight'].cumsum()
        df_cutoff = df.loc[df['weight_cumsum'] <= four_pct_cutoff]
        return (df_cutoff['target'] == 1).sum() / (df['target'] == 1).sum()
        
    def weighted_gini(y_true: pd.DataFrame, y_pred: pd.DataFrame) -> float:
        df = (pd.concat([y_true, y_pred], axis='columns')
              .sort_values('prediction', ascending=False))
        df['weight'] = df['target'].apply(lambda x: 20 if x==0 else 1)
        df['random'] = (df['weight'] / df['weight'].sum()).cumsum()
        total_pos = (df['target'] * df['weight']).sum()
        df['cum_pos_found'] = (df['target'] * df['weight']).cumsum()
        df['lorentz'] = df['cum_pos_found'] / total_pos
        df['gini'] = (df['lorentz'] - df['random']) * df['weight']
        return df['gini'].sum()

    def normalized_weighted_gini(y_true: pd.DataFrame, y_pred: pd.DataFrame) -> float:
        y_true_pred = y_true.rename(columns={'target': 'prediction'})
        return weighted_gini(y_true, y_pred) / weighted_gini(y_true, y_true_pred)

    g = normalized_weighted_gini(y_true, y_pred)
    d = top_four_percent_captured(y_true, y_pred)

    return 0.5 * (g + d)

# KNN

In [57]:
from sklearn.neighbors import KNeighborsClassifier

KNN = KNeighborsClassifier(15)

In [58]:
full_pipeline = Pipeline([
    ("preprocessor", preprocessor),
    ("estimators", KNN),
])

In [59]:
#full_pipeline.fit(X_train, y_train)

In [60]:
#y_pred = full_pipeline.predict_proba(X_eval)

In [61]:
#print(amex_metric(y_pred, y_eval))

In [62]:
from sklearn.metrics import roc_auc_score

#roc_auc_score( y_eval, y_pred[:,1])

# SVM

In [63]:
from sklearn.svm import SVC

svm = SVC(kernel='linear')

In [64]:
full_pipeline = Pipeline([
    ("preprocessor", preprocessor),
    ("estimators", svm),
])

In [65]:
#full_pipeline.fit(X_train, y_train)

In [66]:
#y_pred = full_pipeline.predict_proba(X_eval)

In [67]:
#print(amex_metric(y_pred, y_eval))

In [68]:
from sklearn.metrics import roc_auc_score

#roc_auc_score( y_eval, y_pred[:,1])

# LightGBM

In [69]:
from lightgbm import LGBMClassifier

lgbm = LGBMClassifier(
    n_estimators= 3000, 
    num_leaves= 100,
    learning_rate= 0.01,
    colsample_bytree= 0.6,
    objective = 'binary',
    max_depth= 8,
    min_data_in_leaf = 27,
    bagging_freq = 7,
    bagging_fraction= 0.8,
    feature_fraction = 0.4,
)

In [70]:
full_pipeline = Pipeline([
    ("preprocessor", preprocessor),
    ("estimators", lgbm),
])

In [71]:
#full_pipeline.fit(X_train, y_train)

In [72]:
#y_pred = full_pipeline.predict_proba(X_eval)

In [73]:
#print(amex_metric(y_pred, y_eval))

In [74]:
from sklearn.metrics import roc_auc_score

#roc_auc_score( y_eval, y_pred[:,1])

# Stacked

In [75]:
XGB = XGBClassifier(n_estimators=300, max_depth=6, learning_rate=0.1)

In [76]:
from catboost import CatBoostClassifier

In [77]:
cat = CatBoostClassifier(iterations=3000, random_state=22,
                         learning_rate=0.03,
                         max_depth=9,
                         objective='Logloss',
                         subsample = 0.4,
                         colsample_bylevel=0.3
                        )

In [78]:
from lightgbm import LGBMClassifier
lgbm = LGBMClassifier(

    n_estimators= 3000, 
    num_leaves= 100,
    learning_rate= 0.01,
    colsample_bytree= 0.6,
    objective = 'binary',
    max_depth= 8,
    min_data_in_leaf = 27,
    bagging_freq = 7,
    bagging_fraction= 0.8,
    feature_fraction = 0.4,
)


In [79]:
from sklearn.ensemble import StackingClassifier
from sklearn.linear_model import LogisticRegression

estimators_stacked = [
            
             ('cbc', cat),
            ('lgbm', lgbm),
              #('xbg', XGB)
]    
        


stacked_estimator =  StackingClassifier(estimators=estimators_stacked,
                                    final_estimator= LogisticRegression(),
                                    stack_method='predict_proba'
                                  )

In [80]:
# full_pipeline = Pipeline([
#     ("preprocessor", preprocessor),
#     ("estimators", stacked_estimator),
# ])

In [81]:
import gc
gc.collect()


105

# Output

In [82]:
full_pipeline.fit(Features,target)

[LightGBM] [Warning] feature_fraction is set=0.4, colsample_bytree=0.6 will be ignored. Current value: feature_fraction=0.4
[LightGBM] [Warning] bagging_freq is set=7, subsample_freq=0 will be ignored. Current value: bagging_freq=7
[LightGBM] [Warning] min_data_in_leaf is set=27, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=27
[LightGBM] [Warning] bagging_fraction is set=0.8, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8


Pipeline(steps=[('preprocessor',
                 ColumnTransformer(transformers=[('numeric',
                                                  Pipeline(steps=[('standard_scaler',
                                                                   StandardScaler()),
                                                                  ('imputer',
                                                                   SimpleImputer())]),
                                                  array(['S_2_mean', 'S_2_std', 'S_2_sum', 'S_2_last', 'P_2_mean',
       'P_2_std', 'P_2_sum', 'P_2_last', 'D_39_mean', 'D_39_std',
       'D_39_sum', 'D_39_last', 'B_1_mean', 'B_1_std', 'B_1_sum',
       'B_1_last', 'B_2_mean', 'B...
       'D_126_nunique', 'D_63_last', 'D_63_nunique', 'D_64_last',
       'D_64_nunique', 'D_66_last', 'D_66_nunique', 'D_68_last',
       'D_68_nunique'], dtype=object))])),
                ('estimators',
                 LGBMClassifier(bagging_fraction=0.8, bagging_freq=7,
          

In [83]:

#import numpy as np
#np.mean(cross_val_score(full_pipeline, Features, target, scoring='accuracy', cv=5))


In [84]:
import joblib

joblib.dump(full_pipeline, 'pipes.joblib')

['pipes.joblib']

In [85]:
import joblib
full_pipeline = joblib.load('pipes.joblib')

In [86]:
del train
del Features
gc.collect()

84

In [87]:
test.shape

(924621, 695)

In [88]:
test_probas = full_pipeline.predict_proba(test)

In [89]:
test = pd.read_parquet("/kaggle/input/amex-data-integer-dtypes-parquet-format/test.parquet")

In [90]:
tests = test.groupby('customer_ID').tail(1)

tests.shape

(924621, 190)

In [91]:
test_probas[:,1]

array([0.02605543, 0.00109811, 0.05211299, ..., 0.45155252, 0.2662361 ,
       0.07444415])

In [92]:
tests['prediction']=test_probas[:,1]
tests['prediction']


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


8           0.026055
21          0.001098
34          0.052113
47          0.276969
60          0.853257
              ...   
11363714    0.015328
11363727    0.765696
11363740    0.451553
11363753    0.266236
11363761    0.074444
Name: prediction, Length: 924621, dtype: float64

In [93]:
tests.shape

(924621, 191)

In [94]:
sub = tests[['customer_ID','prediction']]
sub.shape

(924621, 2)

In [95]:
sub.to_csv("my_submission.csv", index=False)
sub.head()

customer_ID  prediction
8   00000469ba478561f23a92a868bd366de6f6527a684c9a...    0.026055
21  00001bf2e77ff879fab36aa4fac689b9ba411dae63ae39...    0.001098
34  0000210045da4f81e5f122c6bde5c2a617d03eef67f82c...    0.052113
47  00003b41e58ede33b8daf61ab56d9952f17c9ad1c3976c...    0.276969
60  00004b22eaeeeb0ec976890c1d9bfc14fd9427e98c4ee9...    0.853257

In [96]:
sub.shape

(924621, 2)

# Parameter tuning

In [97]:
# from sklearn.model_selection import GridSearchCV
# from sklearn.ensemble import StackingClassifier
# from sklearn.linear_model import LogisticRegression

# parameters_gb = {
#   'estimators__lgbm__n_estimators' :[ 2000, 3000, 4000],
#   'estimators__lgbm__max_depth' : [7,8],
#   'estimators__lgbm__learning_rate' : [0.01, 0.02],
#   'estimators__lgbm__bagging_fraction' : [0.6, 0.8],
#   'estimators__lgbm__feature_fraction' : [0.4, 0.6],
# #   'estimator__cbc__n_estimators' :[  2000, 3000, 4000],
# #   'estimator__cbc__max_depth' : [8,9 ],
# #   'estimator__cbc__learning_rate' : [ 0.02, 0.03],
# #   'estimator__cbc__subsample' : [0.4, 0.6],
# #   'estimator__cbc__subsample' : [0.3, 0.5],
# }

# est_xgb = XGBClassifier()
# est_cbc = CatBoostClassifier()
# est_lgbm = LGBMClassifier()

# estimators_st = [
#     ('lgbm', est_lgbm),          
#     ('cbc', est_cbc)
# ]


# stacked_estimator =  StackingClassifier(estimators=estimators_st,
#                                     final_estimator=LogisticRegression,
#                                     stack_method='predict_proba'
#                                   )

# full_pipeline_gs = GridSearchCV(estimator =Pipeline([
#     ("preprocessor", preprocessor),
#     ("estimators",   lgbm)
# ]),  param_grid=parameters_gb)


# #full_pipeline_gs.fit(Features, target)
# # full_pipeline_gs.estimator[1].estimators[0].get_params().keys()
# full_pipeline_gs.estimator.get_params().keys()

In [98]:
# print(" Results from Grid Search ")
# print("\n The best estimator across ALL searched params:\n",full_pipeline_gs.best_estimator_)
# print("\n The best score across ALL searched params:\n",full_pipeline_gs.best_score_)
# print("\n The best parameters across ALL searched params:\n",full_pipeline_gs.best_params_)